In [28]:
#System libraries
import sys
import os
from copy import deepcopy
from inspect import getsource
import pandas as pd
from pathlib import Path
from datetime import datetime
from filelock import FileLock
from itertools import product
from tqdm import tqdm

# Project libraries
from mutations import single_player_swap_2teams, single_player_shift_all_teams, full_position_swap_2teams
from crossovers import crossover_swap_whole_position, crossover_swap_extreme_player
from selection import roulette_selection, tournament_selection, stochastic_selection
from population import *


sys.path.append(os.path.abspath(".."))

In [29]:
def get_best_ind(population):
    fitness_list = [calculate_fitness(team) for team in population if team is not None]
    return population[fitness_list.index(min(fitness_list))]

In [30]:
def log_run_results(
    run_params: dict,
    best_fitness: float,
    csv_path: str = "ga_runs.csv"
) -> None:
    """
    Append one row (hyper-parameters + best_fitness + timestamp) to a CSV file.
    Creates the file with a header the first time it is called.

    Parameters
    ----------
    run_params    : dict   {parameter_name: value}
    best_fitness  : float  best fitness found in the run
    csv_path      : str    path to the CSV log file
    """
    # 1) Build a one-row DataFrame
    row = {**run_params,
           "best_fitness": best_fitness,
           "timestamp": datetime.now()}
    df_new = pd.DataFrame([row])

    # 2) Make sure the folder exists
    csv_path = Path(csv_path)
    csv_path.parent.mkdir(parents=True, exist_ok=True)

    # 3) Simple file lock so parallel runs do not collide
    lock_path = csv_path.with_suffix(csv_path.suffix + ".lock")
    with FileLock(lock_path):
        file_exists = csv_path.is_file()
        mode = "a" if file_exists else "w"
        df_new.to_csv(
            csv_path,
            mode=mode,
            header=not file_exists,   # write header only once
            index=False
        )

In [31]:
# players = load_players_from_csv(r"C:\Users\sacar\OneDrive\Documents\Semester 2 NOVA\CIFO\Labs\CIFO_project_groupA\Data\players(in).csv")
# print(players)

In [32]:

# def run_algorithm(
#         filepath=r"C:\Users\sacar\OneDrive\Documents\Semester 2 NOVA\CIFO\Labs\CIFO_project_groupA\Data\players(in).csv",
#         POP_SIZE=50,
#         max_gen=100,
#         elitism=True,
#         verbose=False,
#         mutation = single_player_swap_2teams,
#         mut_prob=0.2,
#         #Options: single_player_swap_2teams, /
#         # single_player_shift_all teams, /
#         # full_position_swap_2teams
#         crossover = crossover_swap_whole_position,
#         xo_prob=0.8,
#         #Options: crossover_swap_whole_position, /
#         # preset_team_mix_crossover
#         selection_algorithm = tournament_selection,
#         #Options: roulette_selection, /
#         # tournament_selection, /
#         # stoachastic_seleciton
# ):
#     # 1. Initialize a population with N individuals
#     players = load_players_from_csv(filepath)
#     population = generate_population(players, POP_SIZE)

#     # 2. Repeat until termination condition
#     for gen in range(1, max_gen + 1):
#         if verbose:
#             print(f'-------------- Generation: {gen} --------------')

#         # 2.1. Create an empty population P'
#         new_population = []

#         # 2.2. If using elitism, insert best individual from P into P'
#         if elitism:
#             new_population.append(deepcopy(get_best_ind(population)))
        
#         # 2.3. Repeat until P' contains N individuals
#         while len(new_population) < len(population):
#             # 2.3.1. Choose 2 individuals from P using a selection algorithm
#             first_ind = selection_algorithm(population)
#             second_ind = selection_algorithm(population)

#             #if verbose:
#                 #print(f'Selected individuals:\n{first_ind}\n{second_ind}')

#             # 2.3.2. Choose an operator between crossover and replication
#             # 2.3.3. Apply the operator to generate the offspring
#             if random.random() < xo_prob:
#                 offspring1, offspring2 = crossover(first_ind, second_ind)
#                 if verbose:
#                     print(f'Applied {crossover}')
#             else:
#                 offspring1, offspring2 = deepcopy(first_ind), deepcopy(second_ind)
#                 if verbose:
#                     print(f'Applied replication')
            
#             if verbose:
#                 print(f'Offspring:\n{offspring1}\n{offspring2}')
            
#             # 2.3.4. Apply mutation to the offspring
#             first_new_ind = mutation(offspring1, mut_prob)
#             # 2.3.5. Insert the mutated individuals into P'
#             new_population.append(first_new_ind)

#             if verbose:
#                 print(f'First mutated individual: {first_new_ind}')
            
#             if len(new_population) < len(population):
#                 second_new_ind = mutation(offspring2, mut_prob)
#                 new_population.append(second_new_ind)
#                 if verbose:
#                     print(f'Second mutated individual: {first_new_ind}')
        
#         # 2.4. Replace P with P'
#         population = new_population
        
#         # 2.5 . Calculate fitness for each individual in P
#         # fitness_list = []
#         # for team in population:
#             # team.calculate_fitness()
#             # fitness_list.append(team.fitness)
        
#         # best_ind = min(fitness_list)
#         # if verbose:
#             # print(f'Final best individual in generation: {best_ind}')

#     # 3. Return the best individual in P
#     # return best_ind
#         if verbose:
#             print(f'Final best individual in generation: {get_best_ind(population)}')

#     # 3. Return the best individual in P
#     return get_best_ind(population)
# 


In [33]:
def run_algorithm(
    filepath=r"C:\Users\sacar\OneDrive\Documents\Semester 2 NOVA\CIFO\Labs\CIFO_project_groupA\Data\players(in).csv",
    log_path="ga_runs.csv",
    POP_SIZE=50,
    max_gen=100,
    elitism=True,
    verbose=False,
    mutation=single_player_swap_2teams,
    mut_prob=0.2,
    crossover=crossover_swap_whole_position,
    xo_prob=0.8,
    selection_algorithm=tournament_selection
):
    import random
    from copy import deepcopy

    players = load_players_from_csv(filepath)
    population = generate_population(players, POP_SIZE)

    for gen in range(1, max_gen + 1):
        if verbose:
            print(f'-------------- Generation: {gen} --------------')

        new_population = []

        # Elitism
        if elitism:
            try:
                best_ind = deepcopy(get_best_ind(population))
                if best_ind is not None:
                    new_population.append(best_ind)
            except Exception as e:
                if verbose:
                    print(f"Elitism skipped due to error: {e}")

        # Main GA loop
        while len(new_population) < len(population):
            first_ind = selection_algorithm(population)
            second_ind = selection_algorithm(population)

            if not first_ind or not second_ind:
                if verbose:
                    print("Selection returned None. Skipping.")
                continue

            # Crossover or replication
            if random.random() < xo_prob:
                try:
                    offspring_pair = crossover(first_ind, second_ind)
                    if not offspring_pair or len(offspring_pair) != 2:
                        raise ValueError("Crossover failed or returned invalid offspring.")
                    offspring1, offspring2 = offspring_pair
                    if verbose:
                        print(f'Applied {crossover}')
                except Exception as e:
                    if verbose:
                        print(f"Crossover failed: {e}. Using replication instead.")
                    offspring1, offspring2 = deepcopy(first_ind), deepcopy(second_ind)
            else:
                offspring1, offspring2 = deepcopy(first_ind), deepcopy(second_ind)
                if verbose:
                    print(f'Applied replication')

            # Mutation
            try:
                first_new_ind = mutation(offspring1, mut_prob)
                if first_new_ind is not None:
                    new_population.append(first_new_ind)
                    if verbose:
                        print(f'First mutated individual added.')
            except Exception as e:
                if verbose:
                    print(f"Mutation failed for first offspring: {e}")

            if len(new_population) < len(population):
                try:
                    second_new_ind = mutation(offspring2, mut_prob)
                    if second_new_ind is not None:
                        new_population.append(second_new_ind)
                        if verbose:
                            print(f'Second mutated individual added.')
                except Exception as e:
                    if verbose:
                        print(f"Mutation failed for second offspring: {e}")

        population = new_population

        if verbose:
            try:
                print(f'Final best individual in generation {gen}: {get_best_ind(population)}')
            except Exception as e:
                print(f"Could not evaluate best individual: {e}")
    
    best_ind = get_best_ind(population)
    best_fitness = calculate_fitness(best_ind)
    print(f'Final best individual: {best_ind}')
    print(f'Best fitness: {best_fitness}')

    # Log results
    run_params = {
    "POP_SIZE": POP_SIZE,
    "max_gen": max_gen,
    "elitism": elitism,
    "mut_prob": mut_prob,
    "xo_prob": xo_prob,
    "mutation": mutation.__name__,
    "crossover": crossover.__name__,
    "selection_algorithm": selection_algorithm.__name__
}
    log_run_results(run_params, best_fitness, csv_path="ga_runs.csv")

    return best_ind, best_fitness


    


In [34]:
# run_algorithm(
#     filepath=r"C:\Users\sacar\OneDrive\Documents\Semester 2 NOVA\CIFO\Labs\CIFO_project_groupA\Data\players(in).csv",
#     log_path="ga_runs.csv",
#     POP_SIZE=50,
#     max_gen=100,
#     elitism=True,
#     verbose=False,
#     mutation=single_player_shift_all_teams,
#     mut_prob=0.3,
#     crossover=crossover_swap_whole_position,
#     xo_prob=0.8,
#     selection_algorithm=tournament_selection
# )

In [35]:

def run_grid_search():
    # Define the parameter grid
    param_grid = {
        "POP_SIZE": [50, 100],
        "max_gen": [50, 100],
        "mut_prob": [0.1, 0.2, 0.3],
        "xo_prob": [0.7, 0.8, 0.9,],
        "mutation": [single_player_swap_2teams, single_player_shift_all_teams, full_position_swap_2teams],
        "crossover": [crossover_swap_whole_position, crossover_swap_extreme_player],
        "selection_algorithm": [roulette_selection, tournament_selection]
    }

    # Generate all combinations of parameters
    keys = list(param_grid.keys())
    values = (param_grid[key] for key in keys)
    param_combinations = list(product(*values))
    total_runs = len(param_combinations)

    # Progress bar using tqdm
    print(f"Total combinations to run: {total_runs}")
    for i, params in enumerate(tqdm(param_combinations, desc="Grid Search Progress", unit="run")):
        run_params = dict(zip(keys, params))
        print(f"\nRunning combination {i+1}/{total_runs}:")
        for k, v in run_params.items():
            print(f"  {k}: {v.__name__ if callable(v) else v}")
        run_algorithm(**run_params)


In [ ]:
run_grid_search()

Total combinations to run: 432


Grid Search Progress:   0%|          | 0/432 [00:00<?, ?run/s]


Running combination 1/432:
  POP_SIZE: 50
  max_gen: 50
  mut_prob: 0.1
  xo_prob: 0.7
  mutation: single_player_swap_2teams
  crossover: crossover_swap_whole_position
  selection_algorithm: roulette_selection
Swapping all players at position: GK
Swapping all players at position: GK
Swapping all players at position: DEF
Swapping all players at position: MID
Swapping all players at position: FWD
Swapping all players at position: FWD
Swapping all players at position: DEF
Swapping all players at position: DEF
Swapping all players at position: GK
Swapping all players at position: GK
Swapping all players at position: DEF
Swapping all players at position: DEF
Swapping all players at position: MID
Swapping all players at position: MID
Swapping all players at position: DEF
Swapping all players at position: MID
Swapping all players at position: DEF
Swapping all players at position: DEF
Fitness validation failed: Team salary exceeds the cap: 760.0M
Fitness validation failed: Team salary exceeds

Grid Search Progress:   0%|          | 1/432 [00:10<1:18:26, 10.92s/run]

Swapping all players at position: DEF
Swapping all players at position: DEF
Swapping all players at position: MID
Swapping all players at position: FWD
Swapping all players at position: MID
Swapping all players at position: MID
Swapping all players at position: FWD
Swapping all players at position: FWD
Swapping all players at position: GK
Swapping all players at position: DEF
Swapping all players at position: DEF
Final best individual: Ryan Mitchell (GK) - Skill: 83, Cost: 85.0M
Caleb Fisher (DEF) - Skill: 84, Cost: 85.0M
Ethan Howard (DEF) - Skill: 80, Cost: 70.0M
Ashton Phillips (MID) - Skill: 90, Cost: 110.0M
Gavin Richardson (MID) - Skill: 87, Cost: 95.0M
Xavier Bryant (FWD) - Skill: 90, Cost: 120.0M
Colton Gray (FWD) - Skill: 91, Cost: 125.0M

Chris Thompson (GK) - Skill: 80, Cost: 80.0M
Mason Reed (DEF) - Skill: 82, Cost: 75.0M
Owen Parker (DEF) - Skill: 88, Cost: 100.0M
Bentley Rivera (MID) - Skill: 88, Cost: 100.0M
Dylan Morgan (MID) - Skill: 91, Cost: 115.0M
Chase Murphy (FWD)

...

Swapping all players at position: GK
Swapping all players at position: GK
Swapping all players at position: FWD
Final best individual: Ryan Mitchell (GK) - Skill: 83, Cost: 85.0M
Owen Parker (DEF) - Skill: 88, Cost: 100.0M
Lucas Bennett (DEF) - Skill: 85, Cost: 90.0M
Austin Torres (MID) - Skill: 82, Cost: 80.0M
Nathan Wright (MID) - Skill: 92, Cost: 120.0M
Sebastian Perry (FWD) - Skill: 95, Cost: 150.0M
Tyler Jenkins (FWD) - Skill: 80, Cost: 70.0M

Chris Thompson (GK) - Skill: 80, Cost: 80.0M
Jaxon Griffin (DEF) - Skill: 79, Cost: 65.0M
Maxwell Flores (DEF) - Skill: 81, Cost: 72.0M
Dylan Morgan (MID) - Skill: 91, Cost: 115.0M
Bentley Rivera (MID) - Skill: 88, Cost: 100.0M
Elijah Sanders (FWD) - Skill: 93, Cost: 140.0M
Julian Scott (FWD) - Skill: 92, Cost: 130.0M

Blake Henderson (GK) - Skill: 87, Cost: 95.0M
Ethan Howard (DEF) - Skill: 80, Cost: 70.0M
Daniel Foster (DEF) - Skill: 90, Cost: 110.0M
Dominic Bell (MID) - Skill: 86, Cost: 95.0M
Ashton Phillips (MID) - Skill: 90, Cost: 110.0

Grid Search Progress:  23%|██▎       | 98/432 [1:08:49<5:46:35, 62.26s/run]

Swapping all players at position: DEF
Swapping all players at position: FWD
Swapping all players at position: GK
Swapping all players at position: MID
Swapping all players at position: MID
Swapping all players at position: DEF
Swapping all players at position: DEF
Swapping all players at position: DEF
Swapping all players at position: FWD
Swapping all players at position: DEF
Swapping all players at position: MID
Final best individual: Chris Thompson (GK) - Skill: 80, Cost: 80.0M
Brayden Hughes (DEF) - Skill: 87, Cost: 100.0M
Owen Parker (DEF) - Skill: 88, Cost: 100.0M
Ashton Phillips (MID) - Skill: 90, Cost: 110.0M
Austin Torres (MID) - Skill: 82, Cost: 80.0M
Julian Scott (FWD) - Skill: 92, Cost: 130.0M
Zachary Nelson (FWD) - Skill: 86, Cost: 92.0M

Blake Henderson (GK) - Skill: 87, Cost: 95.0M
Logan Brooks (DEF) - Skill: 86, Cost: 95.0M
Daniel Foster (DEF) - Skill: 90, Cost: 110.0M
Bentley Rivera (MID) - Skill: 88, Cost: 100.0M
Spencer Ward (MID) - Skill: 84, Cost: 85.0M
Landon Powel

Grid Search Progress:  23%|██▎       | 99/432 [1:09:11<4:37:39, 50.03s/run]

Final best individual: Blake Henderson (GK) - Skill: 87, Cost: 95.0M
Jaxon Griffin (DEF) - Skill: 79, Cost: 65.0M
Ethan Howard (DEF) - Skill: 80, Cost: 70.0M
Nathan Wright (MID) - Skill: 92, Cost: 120.0M
Hunter Cooper (MID) - Skill: 83, Cost: 85.0M
Elijah Sanders (FWD) - Skill: 93, Cost: 140.0M
Colton Gray (FWD) - Skill: 91, Cost: 125.0M

Ryan Mitchell (GK) - Skill: 83, Cost: 85.0M
Caleb Fisher (DEF) - Skill: 84, Cost: 85.0M
Lucas Bennett (DEF) - Skill: 85, Cost: 90.0M
Dominic Bell (MID) - Skill: 86, Cost: 95.0M
Austin Torres (MID) - Skill: 82, Cost: 80.0M
Xavier Bryant (FWD) - Skill: 90, Cost: 120.0M
Sebastian Perry (FWD) - Skill: 95, Cost: 150.0M

Alex Carter (GK) - Skill: 85, Cost: 90.0M
Owen Parker (DEF) - Skill: 88, Cost: 100.0M
Maxwell Flores (DEF) - Skill: 81, Cost: 72.0M
Dylan Morgan (MID) - Skill: 91, Cost: 115.0M
Connor Hayes (MID) - Skill: 89, Cost: 105.0M
Adrian Collins (FWD) - Skill: 85, Cost: 90.0M
Chase Murphy (FWD) - Skill: 86, Cost: 95.0M

Chris Thompson (GK) - Skill: 